In [5]:
import os
os.chdir('../..')
cwd = os.getcwd()

import json
with open(f'{cwd}/data/files_for_chatGPT/files_for_chatGPT.json') as f:
    file_list = json.load(f)

In [7]:
print(file_list)
def generate_template(id: str, background: str, task: str) -> dict:
    template = {
        "custom_id": id, 
        "method": "POST", 
        "url": "/v1/chat/completions", 
        "body": {
            "model": "gpt-4o-mini", 
            "messages": [
                {
                    "role": "system", 
                    "content": background
                },
                {
                    "role": "user", 
                    "content": task
                }
                        ],
            "max_tokens": 400
                }
    }
    return template

templates = []
background = '''
Du bist ein professioneller Autor, welcher Wetterberichte schreibt. Nun möchtest du deine Wetterberichte in lustig/informell klingende Wetterberichte verwandeln. '''
task = '''
Schreibe bitte folgenden Wetterbericht um:'''
requirements = '''
<requirements>
Der Wetterbericht soll sprachlich warm, liebevoll, malerisch und blümchenhaft sein.
</requirements>

<restrictions>
1. Verwende einfache Sprache.
2. Keine langen Verkettungen von Wörtern oder adjektiven, insbesondere keine langen Zusammensetzungen von Wörtern.
3. Das <city> Token darf nicht verändert werden. Nutze das in der Form exklusiv.
4. Beschränke dich auf die deutsche Sprache.
5. Beschränke dich für Buchstaben auf das deutsche Alphabet, also A-z, ö,ü,ä und ß. Verwende darüber hinaus nur Zeichen aus dem latin-1 Zeichensatz.
6. Nutze nur " als Anführungszeichen.
7. Das Textformat soll genutzt werden um ein Sprachmodell zu trainieren, versuche das allgemeine Vokabular einfach zu halten, ohne seltene Wörter zu benutzen.
8. Beschränke dich auf 150 Wörter.
9. Beschränke dich bei deiner Antwort nur auf den Wetterbericht ohne einleitende oder ausleitende Paragraphe, wie "Hier ist dein Bericht:".  Meine Karriere hängt davon ab!
10. Keine wörtliche Rede.
</restrictions> 
'''
import tqdm
# File to store compressed JSON lines
output_file = f"{cwd}/data/compressed_templates_wout_boeen.jsonl"

# Generate and write compressed templates
with open(output_file, 'w') as out_file:

    for city_file in tqdm.tqdm(file_list):
        city_id = (str(city_file).split('-')[-1]).split('_')[0]  # Extract city id from file name
        with open(f'{cwd}/data/files_for_chatGPT/2024-12-12/{city_file}', encoding='utf-8') as f:
            weather_data = json.load(f)
            city = weather_data['city']
            weather_report = weather_data['report_short']
            weather_report_wout_boeen: str = weather_data['report_short_wout_boeen']
            weather_report_wout_boeen = weather_report_wout_boeen.replace(city, '<city>')
        
        # if weather_report == weather_report_wout_boeen:
        #     continue
        
        # Generate template for this city
        template = generate_template(city_id, background, f'{task} "{weather_report_wout_boeen}" {requirements}')

        # Write template as a single-line JSON to the file
        out_file.write(json.dumps(template) + "\n")


['santa-lucia-UY3440571_standardised.json', 'fontaneda-AD3040437_standardised.json', 'inverness-GB0KM1349_standardised.json', 'puerto-esperanza-AR3429786_standardised.json', 'san-luis-GT3589841_standardised.json', 'gneibet-el-khairi-MR6769369_standardised.json', 'aguaity-PY3439466_standardised.json', 'mbirdiam-SN2248540_standardised.json', 'pir-SN2246670_standardised.json', 'longford-IE2962840_standardised.json', 'tiasso-CI2280758_standardised.json', 'minata-GY3661136_standardised.json', 'villavieja-CO3665898_standardised.json', 'auckland-NZ0AU0002_standardised.json', 'vang-SN2244186_standardised.json', 'trindade-ST2410737_standardised.json', 'san-salvador-CO3668994_standardised.json', 'paso-de-las-carretas-UY3441284_standardised.json', 'los-organos-PE3695161_standardised.json', 'kosarovci-SI10377393_standardised.json', 'ngata-kokokro-CI2288737_standardised.json', 'estancia-santa-filomena-PY3438245_standardised.json', 'west-scarborough-US4982720_standardised.json', 'matasanos-NI3617698

100%|██████████| 19363/19363 [00:04<00:00, 4571.93it/s]


In [8]:
import os

def split_jsonl(input_file, output_dir, max_lines=5000):
    """
    Splits a large JSONL file into smaller JSONL files with a specified maximum number of lines.
    
    Args:
        input_file (str): Path to the input JSONL file.
        output_dir (str): Directory to save the smaller JSONL files.
        max_lines (int): Maximum number of lines per split file. Default is 4000.
    """
    if not os.path.exists(output_dir):
        os.makedirs(output_dir)
    
    with open(input_file, 'r') as infile:
        file_count = 0
        line_count = 0
        current_file = None

        for line in infile:
            if line_count % max_lines == 0:
                if current_file:
                    current_file.close()
                output_file = os.path.join(output_dir, f'split_{file_count}.jsonl')
                current_file = open(output_file, 'w')
                file_count += 1
            
            current_file.write(line)
            line_count += 1

        if current_file:
            current_file.close()

    print(f"Splitting complete. Created {file_count} files in '{output_dir}'.")

# Example usage
input_jsonl_file = f"{cwd}/data/compressed_templates_wout_boeen.jsonl"  # Path to your large JSONL file
output_directory = "batches"      # Directory to store the split files
split_jsonl(input_jsonl_file, output_directory)


Splitting complete. Created 4 files in 'batches'.


In [13]:
import openai
import os
client = openai.OpenAI(api_key="")

os.chdir('../..')
cwd = os.getcwd()
batch_input_file = client.files.create(
file=open(f"{cwd}/batches/split_3.jsonl", "rb"),
purpose="batch"
)

batch_input_file_id = batch_input_file.id
print(batch_input_file_id)

client.batches.create(
  input_file_id=batch_input_file_id,
  endpoint="/v1/chat/completions",
  completion_window="24h",
  metadata={
    "description": "nightly eval job"
  }
)

file-2YTtw8Bo6a4jP86k5ZVV6a


Batch(id='batch_67958c8792c48190b988c7c7e8c296a2', completion_window='24h', created_at=1737854087, endpoint='/v1/chat/completions', input_file_id='file-2YTtw8Bo6a4jP86k5ZVV6a', object='batch', status='validating', cancelled_at=None, cancelling_at=None, completed_at=None, error_file_id=None, errors=None, expired_at=None, expires_at=1737940487, failed_at=None, finalizing_at=None, in_progress_at=None, metadata={'description': 'nightly eval job'}, output_file_id=None, request_counts=BatchRequestCounts(completed=0, failed=0, total=0))

In [14]:
import openai
client = openai.OpenAI(api_key="")

# split 0 batch_676382f75ad48190a2d558d899642954
# split 1 batch_6764f0e2dd288190b50784a1921953f1
# split 2 batch_67662d9c343c8190a36b3d64aaecbe6b
# split 3 batch_676782f234688190a95594753c87d666
# split 4 batch_6768bf8206788190ae1136010d375966
# without Böen batch_676b51596d348190ae540454fa2ad271
# Retrieve the status of the batch job
# new batch with simpler return 
# batch_678649ed00cc8190b7643dd045761c12 - active still
# 
batch_status = client.batches.retrieve(
    'batch_67958c8792c48190b988c7c7e8c296a2'
)

print(batch_status)

Batch(id='batch_67958c8792c48190b988c7c7e8c296a2', completion_window='24h', created_at=1737854087, endpoint='/v1/chat/completions', input_file_id='file-2YTtw8Bo6a4jP86k5ZVV6a', object='batch', status='in_progress', cancelled_at=None, cancelling_at=None, completed_at=None, error_file_id=None, errors=None, expired_at=None, expires_at=1737940487, failed_at=None, finalizing_at=None, in_progress_at=1737854090, metadata={'description': 'nightly eval job'}, output_file_id=None, request_counts=BatchRequestCounts(completed=0, failed=0, total=4363))


In [3]:
response_bytes = client.files.content('file-T781pC9pCNXUfN8TQBgi6W').content.decode('utf-8')
print(response_bytes)

{"id": "batch_req_67917bc63fdc8190ac2d0bf69fff0bc2", "custom_id": "VE0TA0005", "response": {"status_code": 200, "request_id": "a8eee0511536f29447a4c6521034b802", "body": {"id": "chatcmpl-AsduNPvhsWhElbq2Zp8ZN4UWT2oIx", "object": "chat.completion", "created": 1737586483, "model": "gpt-4o-mini-2024-07-18", "choices": [{"index": 0, "message": {"role": "assistant", "content": "In <city> zieht der sanfte Regen seine Bahnen, w\u00e4hrend der Morgen seine Lichter entfaltet. Die Tropfen tanzen auf der Erde und die Temperaturen swingen zwischen 19 und 28\u00b0C. Am Nachmittag umarmt der Himmel die Stadt in sanften Gr\u00fcnt\u00f6nen, w\u00e4hrend der Regen leise weiterflie\u00dft. Wenn die Schatten l\u00e4nger werden, blitzen die Wolken am Himmel, doch der blaue Teppich bleibt erhalten. Die Luft ist frisch, w\u00e4hrend die Temperaturen auf 20 bis 22\u00b0C sinken. In der Nacht kommt der Regen zur\u00fcck, als ob die Wolken ihre Tr\u00e4nen vergie\u00dfen. Sanfte Schauer bringen K\u00fchle und

In [12]:
li = client.batches.list()
for i in li:
    print(i)

Batch(id='batch_6792e3b949f881908e4fadf6a0e40022', completion_window='24h', created_at=1737679801, endpoint='/v1/chat/completions', input_file_id='file-MdqYEkF1sdpordrBupRhr9', object='batch', status='completed', cancelled_at=None, cancelling_at=None, completed_at=1737698216, error_file_id=None, errors=None, expired_at=None, expires_at=1737766201, failed_at=None, finalizing_at=1737697651, in_progress_at=1737679803, metadata={'description': 'nightly eval job'}, output_file_id='file-HbsrZtwwrSZA5dc248fCHY', request_counts=BatchRequestCounts(completed=4363, failed=0, total=4363))
Batch(id='batch_6791707e75e08190bb2713ea34e7206b', completion_window='24h', created_at=1737584766, endpoint='/v1/chat/completions', input_file_id='file-V51hcTuW8mUjGV4vDC75Bq', object='batch', status='completed', cancelled_at=None, cancelling_at=None, completed_at=1737587977, error_file_id=None, errors=None, expired_at=None, expires_at=1737671166, failed_at=None, finalizing_at=1737587653, in_progress_at=173758476

In [1]:
# add output to files

import json
import os

os.chdir('../..')
cwd = os.getcwd()
print(cwd)

gpt_responses = dict()
with open('data/compressed_templates_finished_wout_boen.jsonl', encoding='utf-8') as f:
    for line in f:
        data = json.loads(line)
        gpt_responses[data['custom_id']] = data
print(len(gpt_responses.keys()))

files = {(str(path).split('-')[-1]).split('_')[0]:f'data/files_for_chatGPT/2024-12-12/{path}' for path in os.listdir('data/files_for_chatGPT/2024-12-12')}
print(len(files.keys()))
print(files.keys())

c:\Users\franj\LovelyLLamas
3000
28812
dict_keys(['DO3504833', 'UY3442766', 'PY3436529', 'UY3439661', 'UY3439659', 'AR3833094', 'CH0CH0001', 'DK0NJ0006', 'TD2437703', 'TD2437514', 'HU3056450', 'DO3492129', 'DO3498766', 'DO3500844', 'DO3505796', 'DO3509035', 'MA2562202', 'BR3408424', 'PY3439483', 'NG2353100', 'PE3948642', 'SR3384860', 'BO3924668', 'NE6778046', 'MX3533505', 'MX4019866', 'MX4019867', 'MX4019869', 'UY3480817', 'CF2390694', 'NG2341204', 'US0LA0001', 'US0SC0001', 'CA5881791', 'AR3867042', 'ML2596472', 'VE3649859', 'CO3690592', 'GH2306405', 'GH2306406', 'SR3384857', 'BS3572946', 'AG3576398', 'GB0KM0009', 'US0MS0002', 'US0SD0001', 'GB0KL0046', 'GH2306382', 'US0KS0002', 'US0TX0003', 'JM3491623', 'GH2589879', 'CI2293520', 'CI2293519', 'CI2293518', 'GH2306298', 'NG2352857', 'NG10275569', 'CI2284679', 'BJ11497769', 'GH2306250', 'TD0245732', 'AR3867009', 'SR8220906', 'BS0MG0001', 'CA5881990', 'CL3900742', 'PT0SA0001', 'PT2743428', 'VE3649853', 'DO3497543', 'DO3504267', 'DO3508326',

In [2]:
import tqdm
for value in tqdm.tqdm(gpt_responses.values()):
    identifier = value['custom_id']
    path = files[identifier]
    gpt_response = value['response']['body']['choices'][0]['message']['content']
    
    with open(path, 'r', encoding='utf-8') as f:
        data = json.load(f)


    data['gpt_rewritten_informell'] = gpt_response

    with open(path, 'w', encoding='utf-8') as f:
        json.dump(data, f, ensure_ascii=False, indent=4)
    # print(identifier, path, gpt_response)

  0%|          | 0/3000 [00:00<?, ?it/s]

100%|██████████| 3000/3000 [00:24<00:00, 120.63it/s]
